# Identity matrix vs. Hessian matrix

**Date:** 18 April 2025

**Objective:** In this notebook, we compare two matrix types in `IntegrationProfiler`:
- matrix_type = :hessian,
- matrix_type = :identity (with 5 choices of gamma: 1e-1, 1e+0, 1e+2, 1e+4, 1e6).

Our criteria for comparison are:
- Number of function evaluations
- Running time

**Results:** 
- The trend seems that there is a tradeoff. Larger gamma means better accuracy. Larger gamma means more function evaluations.
- For integration profiler with matrix_type = :identity, set gamma close to 1 for best performance.
- For integration profiler with matrix_type = :identity, set larger gamma (1e4..1e6) for best accuracy.

**Questions:**
- How the choice of integrator and integrator options is made? Does it affect results (and how)?

### 1. Load packages

In [1]:
using Revise
using LikelihoodProfiler
using Optimization, ForwardDiff, OrdinaryDiffEq
using CSV, DataFrames, PrettyTables
using Plots

### 2. Analysis for simple analytic functions

In a first experiment, we run different methods for simple analytic functions.

In [2]:
include(joinpath(@__DIR__, "../models/AnalyticFuncs/analytic_funcs.jl"))

Dict{Symbol, Dict{Symbol, Any}} with 8 entries:
  :f_5p       => Dict(:threshold=>4.0, :profile_range=>[(-20.0, 20.0), (-20.0, …
  :f_3p_1im   => Dict(:grad!=>#23, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :f_4p_2im   => Dict(:grad!=>#29, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :f_1p_ex    => Dict(:grad!=>#14, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :f_3p_1im2  => Dict(:grad!=>#26, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :f_2p_1im   => Dict(:grad!=>#17, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :f_2p       => Dict(:grad!=>#20, :threshold=>4.0, :profile_range=>[(-20.0, 20…
  :rosenbrock => Dict(:threshold=>4.0, :profile_range=>[(-10.0, 10.0), (-10.0, …

In [2]:
integrator = Tsit5()
integrator_opts = (dtmax=0.3,)

(dtmax = 0.3,)

In [3]:
function get_methods(integrator, integrator_opts)
    method1 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :hessian)
    method2 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :identity, gamma = 1e-1)
    method3 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :identity, gamma = 1e+0)
    method4 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :identity, gamma = 1e+2)
    method5 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :identity, gamma = 1e+4)
    method6 = IntegrationProfiler(integrator = integrator, integrator_opts = integrator_opts, matrix_type = :identity, gamma = 1e+6)
    methods = [method1, method2, method3, method4, method5, method6]
end

get_methods (generic function with 1 method)

In [8]:
function run1()
all_results = []
for (name, infos) in funcs_dict
    optf = OptimizationFunction(infos[:func], AutoForwardDiff())
    optprob = OptimizationProblem(optf, infos[:optim])
    plprob = PLProblem(
        optprob, 
        infos[:optim], 
        infos[:profile_range]; 
        threshold = infos[:threshold]
    )

    methods = get_methods(integrator, integrator_opts)
    results = []
    for method in methods
        try
            time = @elapsed sol = profile(plprob, method)
            push!(results, (method=method, sol=sol, time=time))
        catch e
            println(method, "\n  ", e)
        end
    end

    df = []
    for result in results
        push!(df, [
            (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
            map(i -> (s=result.sol[i].stats; s[1].nf+s[2].nf), 1:length(result.sol)),
            result.time
        ])
    end

    pretty_table(
        permutedims(reduce(hcat, df)),
        header=["method", "fevals", "runtime"],
        title=string(name)
    )
    
    push!(all_results, (name=name, results=results))
end
all_results
end

all_results = run1()

f_5p
┌────────────────────────────────────────────┬───────────┬───────────┐
│                                     method │    fevals │   runtime │
├────────────────────────────────────────────┼───────────┼───────────┤
│      (matrix_type = :hessian, gamma = 1.0) │ [90, 126] │  0.001168 │
│     (matrix_type = :identity, gamma = 0.1) │ [72, 126] │ 0.0009014 │
│     (matrix_type = :identity, gamma = 1.0) │ [72, 126] │ 0.0007338 │
│   (matrix_type = :identity, gamma = 100.0) │ [72, 126] │ 0.0006987 │
│ (matrix_type = :identity, gamma = 10000.0) │ [72, 126] │ 0.0005557 │
│   (matrix_type = :identity, gamma = 1.0e6) │ [72, 126] │ 0.0005258 │
└────────────────────────────────────────────┴───────────┴───────────┘
f_3p_1im
┌────────────────────────────────────────────┬───────────────────────┬───────────┐
│                                     method │                fevals │   runtime │
├────────────────────────────────────────────┼───────────────────────┼───────────┤
│      (matrix_type = :hess

8-element Vector{Any}:
 (name = :f_5p, results = Any[(method = IntegrationProfiler{Nothing, @NamedTuple{}, Tsit5{typeof(OrdinaryDiffEqCore.trivial_limiter!), typeof(OrdinaryDiffEqCore.trivial_limiter!), Static.False}, @NamedTuple{dtmax::Float64}}(false, nothing, NamedTuple(), Tsit5{typeof(OrdinaryDiffEqCore.trivial_limiter!), typeof(OrdinaryDiffEqCore.trivial_limiter!), Static.False}(OrdinaryDiffEqCore.trivial_limiter!, OrdinaryDiffEqCore.trivial_limiter!, static(false)), (dtmax = 0.3,), :hessian, 1.0), sol = LikelihoodProfiler.PLSolution{PLProblem{LikelihoodProfiler.ParameterProfile, OptimizationProblem{true, OptimizationFunction{true, AutoForwardDiff{nothing, Nothing}, var"#32#56", Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, typeof(SciMLBase.DEFAULT_OBSERVED_NO_TIME), Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing}, Vector{Float64}, SciMLBase.NullParameters, Nothing, Not

- For two systems, `f_3p_1im` and `rosenbrock`, the number of function evaluations increases by a lot for larger gammas, and (seems to) lead to slower running time.
- For other systems, the number of function evaluations is stable.

### 3. Analysis for Taxol

In [9]:
integrator = FBDF(autodiff = AutoFiniteDiff())
integrator_opts = (;)

NamedTuple()

In [11]:
include(joinpath(@__DIR__, "../models/Taxol/taxol_model.jl"))
optf = OptimizationFunction(taxol_obj, Optimization.AutoForwardDiff())
optprob = OptimizationProblem(optf, p0)
profile_range = [
  (2., 30.),
  (2.0, 30.),
  (0.01, 0.6),
  (0.05, 5.),
  (30., 250.)
]
plprob = PLProblem(optprob, p0, profile_range; threshold = sigmasq*chi2_quantile(0.95, 5))

Profile Likelihood Problem. Profile type: parameter
Parameters' optimal values: 
5-element Vector{Float64}:
   8.317
   8.0959
   0.0582
   1.3307
 119.1363

In [12]:
function run2()
methods = get_methods(integrator, integrator_opts)
results = []
for method in methods
    try
        time = @elapsed sol = profile(plprob, method)
        push!(results, (method=method, sol=sol, time=time))
    catch e
        println(method, "\n  ", e)
    end
end

df = []
for result in results
    push!(df, [
        (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
        map(i -> (s=result.sol[i].stats; s[1].nf+s[2].nf), 1:length(result.sol)),
        result.time
    ])
end

pretty_table(
    permutedims(reduce(hcat, df)),
    header=["method", "fevals", "runtime"],
    title=string("Taxol")
)
results
end

results = run2()

Taxol
┌────────────────────────────────────────────┬───────────────────────────────┬─────────┐
│                                     method │                        fevals │ runtime │
├────────────────────────────────────────────┼───────────────────────────────┼─────────┤
│      (matrix_type = :hessian, gamma = 1.0) │     [346, 228, 635, 261, 269] │ 73.3492 │
│     (matrix_type = :identity, gamma = 0.1) │     [194, 133, 143, 196, 330] │ 21.5614 │
│     (matrix_type = :identity, gamma = 1.0) │     [336, 145, 141, 218, 496] │ 5.08858 │
│   (matrix_type = :identity, gamma = 100.0) │     [476, 370, 324, 331, 972] │ 7.19014 │
│ (matrix_type = :identity, gamma = 10000.0) │    [690, 825, 498, 466, 1122] │ 10.4358 │
│   (matrix_type = :identity, gamma = 1.0e6) │ [1204, 2260, 1374, 546, 1174] │ 15.0863 │
└────────────────────────────────────────────┴───────────────────────────────┴─────────┘


6-element Vector{Any}:
 (method = IntegrationProfiler{Nothing, @NamedTuple{}, FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}, @NamedTuple{}}(false, nothing, NamedTuple(), FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}(Val{5}(), nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}(1//100, 10, 1//5, 1//5, false, true, 0//1), OrdinaryDiffEqCore.DEFAULT_PRECS, nothing, nothing, :linear, :Standard, OrdinaryDiffEqCore.tri

The tendency seems to be that for larger gammas we have more function evaluations (and, perhaps, as a consequence, larger runtime).

We then check for all methods if the CI and trajectories are computed correctly, visually and quantitatively.

In [48]:
truth = results[1]
df = []
for result in results
    push!(df, [
        (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
        map(i -> (result.sol[i].endpoints), 1:length(result.sol))...
    ])
end
function calc_error(x_endpoint, truth_endpoint)
    if truth_endpoint == nothing || x_endpoint == nothing
        return x_endpoint == truth_endpoint ? 0 : Inf
    end
    round(abs(truth_endpoint - x_endpoint), digits=2)
end
df_errors = [
    [result[1], [calc_error.(result[i], truth.sol[i-1].endpoints) for i in 2:length(result)]...]
    for result in df
]
pretty_table(
    permutedims(reduce(hcat, df)),
    header=["method", ["x_$i" for i in 1:length(truth.sol)]...],
    title=string("Taxol CI")
)
pretty_table(
    permutedims(reduce(hcat, df_errors)),
    header=["method", ["x_$(i)_err" for i in 1:length(truth.sol)]...],
    title=string("Taxol CI Errors")
)

Taxol CI
┌────────────────────────────────────────────┬────────────────────┬────────────────────┬───────────────────────┬─────────────────────┬────────────────────┐
│                                     method │                x_1 │                x_2 │                   x_3 │                 x_4 │                x_5 │
├────────────────────────────────────────────┼────────────────────┼────────────────────┼───────────────────────┼─────────────────────┼────────────────────┤
│      (matrix_type = :hessian, gamma = 1.0) │ (6.67879, 17.2971) │  (4.95518, 10.728) │   (nothing, 0.405737) │ (0.187184, nothing) │ (49.4394, nothing) │
│     (matrix_type = :identity, gamma = 0.1) │ (6.86389, 11.8003) │ (5.88174, 10.5071) │ (0.0209772, 0.097982) │ (0.516514, 4.58386) │  (53.0263, 224.76) │
│     (matrix_type = :identity, gamma = 1.0) │ (6.80616, 17.2686) │  (5.7189, 10.6416) │ (0.0198099, 0.100343) │ (0.501454, nothing) │ (50.1956, nothing) │
│   (matrix_type = :identity, gamma = 100.0) │ (6.67285

We observe that, roughly speaking, the accuracy of CIs increases with the increase of gamma.

Plotting results:

1. ground truth

In [22]:
@info "(matrix_type=$(results[1].method.matrix_type), gamma=$(results[1].method.gamma))"
plot(results[1].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=hessian, gamma=1.0)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X22sZmlsZQ==.jl:1


2. gamma = 1e-1

Note that x[3] changes from non-identifiable to identifiable and x[4], x[5] change from identifiable to non-identifiable.

In [23]:
@info "(matrix_type=$(results[2].method.matrix_type), gamma=$(results[2].method.gamma))"
plot(results[2].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=identity, gamma=0.1)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X23sZmlsZQ==.jl:1


3. gamma = 1e-0

Note that x[3] changes from non-identifiable to identifiable

In [24]:
@info "(matrix_type=$(results[3].method.matrix_type), gamma=$(results[3].method.gamma))"
plot(results[3].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=identity, gamma=1.0)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X24sZmlsZQ==.jl:1


4. gamma = 1e+2

Verdicts about identifiability are correct.

In [25]:
@info "(matrix_type=$(results[4].method.matrix_type), gamma=$(results[4].method.gamma))"
plot(results[4].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=identity, gamma=100.0)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X25sZmlsZQ==.jl:1


5. gamma = 1e+4

Verdicts about identifiability are correct.

In [26]:
@info "(matrix_type=$(results[5].method.matrix_type), gamma=$(results[5].method.gamma))"
plot(results[5].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=identity, gamma=10000.0)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X26sZmlsZQ==.jl:1


6. gamma = 1e+6

Verdicts about identifiability are correct.

We observe some artifacts on the trajectory.

In [27]:
@info "(matrix_type=$(results[6].method.matrix_type), gamma=$(results[6].method.gamma))"
plot(results[6].sol, size=(700,400), dpi=1)

┌ Info: (matrix_type=identity, gamma=1.0e6)
└ @ Main c:\data\projects\insysbio\LikelihoodProfiler.jl\reports\jl_notebook_cell_df34fa98e69747e1a8f8a730347b8e2f_X30sZmlsZQ==.jl:1


### 3. Analysis for SIR

In [30]:
integrator = FBDF(autodiff = AutoFiniteDiff())
integrator_opts = (;)

NamedTuple()

In [40]:
include(joinpath(@__DIR__, "../Models/SIR/sir_model.jl"))
optf = OptimizationFunction(sir_obj, Optimization.AutoForwardDiff())
optprob = OptimizationProblem(optf, p0)
optpars = [0.3998583528283355, 0.24676816253516404, 1.2460180516141481e-5]
plprob = PLProblem(optprob, optpars, (-20.,20.); threshold = chi2_quantile(0.95, 3)/2)

Profile Likelihood Problem. Profile type: parameter
Parameters' optimal values: 
3-element Vector{Float64}:
 0.3998583528283355
 0.24676816253516404
 1.2460180516141481e-5

In [41]:
function run3()
methods = get_methods(integrator, integrator_opts)
results = []
for method in methods
    try
        time = @elapsed sol = profile(plprob, method)
        push!(results, (method=method, sol=sol, time=time))
    catch e
        println(method, "\n  ", e)
    end
end

df = []
for result in results
    push!(df, [
        (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
        map(i -> (s=result.sol[i].stats; s[1].nf+s[2].nf), 1:length(result.sol)),
        result.time
    ])
end

pretty_table(
    permutedims(reduce(hcat, df)),
    header=["method", "fevals", "runtime"],
    title=string("SIR")
)
results
end
    
results = run3()

1-element Vector{Any}:
 (method = IntegrationProfiler{Nothing, @NamedTuple{}, FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}, @NamedTuple{}}(false, nothing, NamedTuple(), FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}(Val{5}(), nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}(1//100, 10, 1//5, 1//5, false, true, 0//1), OrdinaryDiffEqCore.DEFAULT_PRECS, nothing, nothing, :linear, :Standard, OrdinaryDiffEqCore.tri

It seems that the integrator fails for identity matrix for all choices of gamma. 

### 4. Analysis for JAK-STAT

In [4]:
integrator = FBDF(autodiff = AutoFiniteDiff())
integrator_opts = (;)

NamedTuple()

In [5]:
include(joinpath(@__DIR__, "../Models/JakStat/jak-stat_model.jl"))
optpars = log10.(p_best)
optf = OptimizationFunction(jakstat_obj, Optimization.AutoForwardDiff())
optprob = OptimizationProblem(optf, optpars)
profile_range = [
  (-3.,3.),
  (-6.,4.),
  (-3.,3.),
  (-3.,3),
  (0., 6.),
  (2., 6.),
  (0., 2.),
  (0., 2.),
  (0., 2.)
]
plprob = PLProblem(optprob, optpars, profile_range; threshold = chi2_quantile(0.95, 1))

Profile Likelihood Problem. Profile type: parameter
Parameters' optimal values: 
9-element Vector{Float64}:
 -1.5689175883999988
 -4.999704893599998
 -2.2096987817000167
 -1.78600654750001
  4.9901140088
  4.1977354885
  0.5857552705999998
  0.8189828191999999
  0.49868440400000047

In [6]:
function run4()
methods = get_methods(integrator, integrator_opts)
results = []
for method in methods
    try
        time = @elapsed sol = profile(plprob, method)
        push!(results, (method=method, sol=sol, time=time))
    catch e
        println(method, "\n  ", e)
    end
end

df = []
for result in results
    push!(df, [
        (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
        map(i -> (s=result.sol[i].stats; s[1].nf+s[2].nf), 1:length(result.sol)),
        result.time
    ])
end

pretty_table(
    permutedims(reduce(hcat, df)),
    header=["method", "fevals", "runtime"],
    title=string("JAK-STAT")
)
results
end
    
results = run4()

┌ Warning: First function call produced NaNs. Exiting. Double check that none of the initial conditions, parameters, or timespan values are NaN.
└ @ OrdinaryDiffEqCore C:\Users\User\.julia\packages\OrdinaryDiffEqCore\bMOsj\src\initdt.jl:131
┌ Warning: At t=0.0, dt was forced below floating point epsilon 5.0e-324, and step error estimate = NaN. Aborting. There is either an error in your model specification or the true solution is unstable (or the true solution can not be represented in the precision of ForwardDiff.Dual{ForwardDiff.Tag{typeof(jakstat_obj), Float64}, Float64, 9}).
└ @ SciMLBase C:\Users\User\.julia\packages\SciMLBase\c6Noy\src\integrator_interface.jl:623


JAK-STAT
┌────────────────────────────────────────────┬───────────────────────────────────────────────┬─────────┐
│                                     method │                                        fevals │ runtime │
├────────────────────────────────────────────┼───────────────────────────────────────────────┼─────────┤
│      (matrix_type = :hessian, gamma = 1.0) │ [182, 189, 229, 185, 195, 121, 143, 138, 125] │ 538.687 │
│     (matrix_type = :identity, gamma = 0.1) │ [285, 149, 212, 242, 183, 191, 240, 205, 168] │  67.648 │
│     (matrix_type = :identity, gamma = 1.0) │ [251, 131, 259, 224, 211, 217, 248, 175, 186] │ 74.1133 │
│   (matrix_type = :identity, gamma = 100.0) │ [314, 180, 270, 270, 307, 229, 246, 189, 203] │ 80.4438 │
│ (matrix_type = :identity, gamma = 10000.0) │ [337, 216, 450, 413, 344, 320, 416, 332, 335] │ 80.1784 │
│   (matrix_type = :identity, gamma = 1.0e6) │ [574, 301, 486, 546, 383, 475, 617, 502, 548] │ 106.737 │
└────────────────────────────────────────────┴

6-element Vector{Any}:
 (method = IntegrationProfiler{Nothing, @NamedTuple{}, FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}, @NamedTuple{}}(false, nothing, NamedTuple(), FBDF{5, 0, AutoFiniteDiff{Val{:forward}, Val{:forward}, Val{:hcentral}, Nothing, Nothing, Bool}, Nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}, typeof(OrdinaryDiffEqCore.DEFAULT_PRECS), Val{:forward}(), true, nothing, Nothing, Nothing, typeof(OrdinaryDiffEqCore.trivial_limiter!)}(Val{5}(), nothing, NLNewton{Rational{Int64}, Rational{Int64}, Rational{Int64}, Rational{Int64}}(1//100, 10, 1//5, 1//5, false, true, 0//1), OrdinaryDiffEqCore.DEFAULT_PRECS, nothing, nothing, :linear, :Standard, OrdinaryDiffEqCore.tri

Again, larger gammas seem to lead to more function evaluations.

Let us check the CIs and trajectories.

In [7]:
truth = results[1]
df = []
for result in results
    push!(df, [
        (matrix_type=result.method.matrix_type, gamma=result.method.gamma), 
        map(i -> (result.sol[i].endpoints), 1:length(result.sol))...
    ])
end
function calc_error(x_endpoint, truth_endpoint)
    if truth_endpoint == nothing || x_endpoint == nothing
        return x_endpoint == truth_endpoint ? 0 : Inf
    end
    round(abs(truth_endpoint - x_endpoint), digits=2)
end
df_errors = [
    [result[1], [calc_error.(result[i], truth.sol[i-1].endpoints) for i in 2:length(result)]...]
    for result in df
]
pretty_table(
    permutedims(reduce(hcat, df)),
    header=["method", ["x_$i" for i in 1:length(truth.sol)]...],
    title=string("JAK-STAK CI")
)
pretty_table(
    permutedims(reduce(hcat, df_errors)),
    header=["method", ["x_$(i)_err" for i in 1:length(truth.sol)]...],
    title=string("JAK-STAK CI Errors")
)

JAK-STAK CI
┌────────────────────────────────────────────┬──────────────────────┬─────────────────────┬──────────────────────┬──────────────────────┬─────────────────────┬────────────────────┬──────────────────────┬──────────────────────┬──────────────────────┐
│                                     method │                  x_1 │                 x_2 │                  x_3 │                  x_4 │                 x_5 │                x_6 │                  x_7 │                  x_8 │                  x_9 │
├────────────────────────────────────────────┼──────────────────────┼─────────────────────┼──────────────────────┼──────────────────────┼─────────────────────┼────────────────────┼──────────────────────┼──────────────────────┼──────────────────────┤
│      (matrix_type = :hessian, gamma = 1.0) │  (-1.72838, -1.4034) │ (nothing, -3.04532) │  (-2.5318, -1.92295) │  (-1.90217, -1.6663) │ (0.160736, nothing) │ (4.11241, 4.28885) │ (0.421673, 0.776935) │ (0.675509, 0.997353) │ (0.358166, 

Interestingly, there are very small errors for gamma=1e-1, and essentially no errors (<1%) for gamma >= 1. 